In [75]:
%matplotlib inline
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function
import matplotlib.pyplot as plt
import tensorflow as tf
import numpy as np
from sklearn.metrics import confusion_matrix
import cv2, os, math, time
from datetime import timedelta
from sklearn.utils import shuffle
from shutil import copyfile, move, copytree, copy2, rmtree
import shutil

In [4]:
###Configuration
"""
Data Configurations/Paths
"""
img_dir_patches="./SD/patched_images"
img_dir_originals = "../../original_images/SD"
img_dir_same = img_dir + "/1"
img_dir_diff = img_dir + "/0"

##
# Convolutional Layer 1.
filter_size1 = 4          # Convolution filters are 4 x 4 pixels.
num_filters1 = 16         # There are 16 of these filters.

# Convolutional Layer 2.
filter_size2 = 2          # Convolution filters are 2 x 2 pixels.
num_filters2 = 32         # There are 32 of these filters.

# Convolutional Layer 3.
filter_size3 = 2          # Convolution filters are 2 x 2 pixels.
num_filters3 = 64         # There are 64 of these filters.

# Convolutional Layer 4.
filter_size4 = 2          # Convolution filters are 2 x 2 pixels.
num_filters4 = 128         # There are 128 of these filters.

# Fully-connected layer.
fc_size = 256             # Number of neurons in fully-connected layer.

# We know that images are 60 pixels in each dimension.
img_size = 4*2

# Images are stored in one-dimensional arrays of this length.
img_size_flat = 4 * 2

# Number of colour channels for the images: 3 channel for RGB.
num_channels = 3

# Tuple with height and width of images used to reshape arrays.
img_shape = (4, 2, num_channels)


# Number of classes, one class for same and one for different image
num_classes = 2

NameError: name 'img_dir' is not defined

In [89]:
def load_data(img_dir, img_type="patches"):
        list_of_imgs = []
        list_same_diff = []
        for img_no in os.listdir(img_dir):
            if img_no == ".DS_Store":
                continue

            img_no_path = os.path.join(img_dir, img_no)
            for img_label in os.listdir(img_no_path):
                if img_label == ".DS_Store":
                    continue
                    
                list_same_diff.append(int(img_label))
                img_lbl_path = os.path.join(img_no_path, img_label)
                
                if img_type == "originals":
                    img_lbl_path = img_lbl_path + "/img/"
                
                for img in os.listdir(img_lbl_path):
                    img_path = os.path.join(img_lbl_path, img)
                    list_of_imgs.append(img_path)

        data_imgs = np.array(list_of_imgs)
        data_same_diff = np.array(list_same_diff)

        return data_imgs, data_same_diff

    
def get_batch_images(data, same_diff, rshp):
        list_of_imgs = []
        list_of_same_diff = []
        for img, img_type in zip(data, same_diff):
            orig_img = cv2.imread(img)
#             print(orig_img.shape, type(orig_img.shape))
            #only first image as a label
            if orig_img is None:
                    print ("Unable to read image{}".format(img))
                    continue
            
            if orig_img.shape == (4, 2, 3):
                flattened_img = orig_img.flatten()
                list_of_imgs.append(np.asarray(flattened_img, dtype=np.float32))
                
                if img_type == 1: #0 is same and 1 is different
                    list_of_same_diff.append([0,1])
                else:
                    list_of_same_diff.append([1,0])
        
        data_imgs = np.array(list_of_imgs)
        data_img_type = np.array(list_of_same_diff)
        
#         print(len(data_imgs), len(data_img_type), data_img_type.shape)
        
        return data_imgs, data_img_type

def copytree(src, dst, symlinks=False, ignore=None):
    for item in os.listdir(src):
        s = os.path.join(src, item)
        d = os.path.join(dst, item)
        if os.path.isdir(s):
            shutil.copytree(s, d, symlinks, ignore)
        else:
            shutil.copy2(s, d)    
    
def copy_valid_images(data):
    for img in zip(data):
        orig_img_path = "../../original_images/SD/"
        dest_path = "./SD/original_images/"
        img = str(img[0])
        mv_dir = img.split("SD/patched_images/")[1].split("/")[0]
        if mv_dir == ".DS_Store":
            continue
            
        if cv2.imread(img).shape == (4, 2, 3):
            dest_path = dest_path + mv_dir
            src_dir = orig_img_path + mv_dir
#             print(mv_dir)
#             print(src_dir)
#             print(dest_path)
            
            copytree(src_dir,dest_path)
        else:
            rmtree("./SD/patched_images/" + mv_dir)

In [90]:
copy_valid_images(train_data)

In [49]:
train_data, train_lbls = load_data(img_dir_patches)

./SD/patched_images/39386/1
./SD/patched_images/39386/1/img.png
./SD/patched_images/38254/0
./SD/patched_images/38254/0/img.png
./SD/patched_images/1069/1
./SD/patched_images/1069/1/img.png
./SD/patched_images/21379/0
./SD/patched_images/21379/0/img.png
./SD/patched_images/1855/1
./SD/patched_images/1855/1/img.png
./SD/patched_images/30805/0
./SD/patched_images/30805/0/img.png
./SD/patched_images/34499/0
./SD/patched_images/34499/0/img.png
./SD/patched_images/26960/1
./SD/patched_images/26960/1/img.png
./SD/patched_images/29114/1
./SD/patched_images/29114/1/img.png
./SD/patched_images/30039/0
./SD/patched_images/30039/0/img.png
./SD/patched_images/9204/1
./SD/patched_images/9204/1/img.png
./SD/patched_images/48123/1
./SD/patched_images/48123/1/img.png
./SD/patched_images/18653/1
./SD/patched_images/18653/1/img.png
./SD/patched_images/797/1
./SD/patched_images/797/1/img.png
./SD/patched_images/47957/0
./SD/patched_images/47957/0/img.png
./SD/patched_images/46885/1
./SD/patched_images/46

./SD/patched_images/41895/0
./SD/patched_images/41895/0/img.png
./SD/patched_images/15379/0
./SD/patched_images/15379/0/img.png
./SD/patched_images/45409/1
./SD/patched_images/45409/1/img.png
./SD/patched_images/37029/1
./SD/patched_images/37029/1/img.png
./SD/patched_images/40947/1
./SD/patched_images/40947/1/img.png
./SD/patched_images/39381/0
./SD/patched_images/39381/0/img.png
./SD/patched_images/15977/0
./SD/patched_images/15977/0/img.png
./SD/patched_images/32769/1
./SD/patched_images/32769/1/img.png
./SD/patched_images/38253/0
./SD/patched_images/38253/0/img.png
./SD/patched_images/40349/1
./SD/patched_images/40349/1/img.png
./SD/patched_images/10439/0
./SD/patched_images/10439/0/img.png
./SD/patched_images/14099/1
./SD/patched_images/14099/1/img.png
./SD/patched_images/1852/1
./SD/patched_images/1852/1/img.png
./SD/patched_images/23429/0
./SD/patched_images/23429/0/img.png
./SD/patched_images/48918/0
./SD/patched_images/48918/0/img.png
./SD/patched_images/30802/0
./SD/patched_i

./SD/patched_images/46427/0
./SD/patched_images/46427/0/img.png
./SD/patched_images/7700/1
./SD/patched_images/7700/1/img.png
./SD/patched_images/13625/0
./SD/patched_images/13625/0/img.png
./SD/patched_images/309/0
./SD/patched_images/309/0/img.png
./SD/patched_images/27410/0
./SD/patched_images/27410/0/img.png
./SD/patched_images/2272/1
./SD/patched_images/2272/1/img.png
./SD/patched_images/43155/0
./SD/patched_images/43155/0/img.png
./SD/patched_images/42087/1
./SD/patched_images/42087/1/img.png
./SD/patched_images/8748/1
./SD/patched_images/8748/1/img.png
./SD/patched_images/31575/1
./SD/patched_images/31575/1/img.png
./SD/patched_images/17043/1
./SD/patched_images/17043/1/img.png
./SD/patched_images/2888/0
./SD/patched_images/2888/0/img.png
./SD/patched_images/23276/0
./SD/patched_images/23276/0/img.png
./SD/patched_images/6414/1
./SD/patched_images/6414/1/img.png
./SD/patched_images/18837/0
./SD/patched_images/18837/0/img.png
./SD/patched_images/47733/1
./SD/patched_images/47733/

./SD/patched_images/41053/0
./SD/patched_images/41053/0/img.png
./SD/patched_images/39149/1
./SD/patched_images/39149/1/img.png
./SD/patched_images/14251/0
./SD/patched_images/14251/0/img.png
./SD/patched_images/20064/1
./SD/patched_images/20064/1/img.png
./SD/patched_images/5606/0
./SD/patched_images/5606/0/img.png
./SD/patched_images/44521/0
./SD/patched_images/44521/0/img.png
./SD/patched_images/36101/1
./SD/patched_images/36101/1/img.png
./SD/patched_images/15383/0
./SD/patched_images/15383/0/img.png
./SD/patched_images/39975/1
./SD/patched_images/39975/1/img.png
./SD/patched_images/1094/1
./SD/patched_images/1094/1/img.png
./SD/patched_images/33641/0
./SD/patched_images/33641/0/img.png
./SD/patched_images/41261/1
./SD/patched_images/41261/1/img.png
./SD/patched_images/32793/1
./SD/patched_images/32793/1/img.png
./SD/patched_images/25724/0
./SD/patched_images/25724/0/img.png
./SD/patched_images/11511/0
./SD/patched_images/11511/0/img.png
./SD/patched_images/5434/0
./SD/patched_imag

./SD/patched_images/13443/1
./SD/patched_images/13443/1/img.png
./SD/patched_images/27676/0
./SD/patched_images/27676/0/img.png
./SD/patched_images/2014/1
./SD/patched_images/2014/1/img.png
./SD/patched_images/43333/1
./SD/patched_images/43333/1/img.png
./SD/patched_images/49609/1
./SD/patched_images/49609/1/img.png
./SD/patched_images/31713/1
./SD/patched_images/31713/1/img.png
./SD/patched_images/19179/1
./SD/patched_images/19179/1/img.png
./SD/patched_images/12591/0
./SD/patched_images/12591/0/img.png
./SD/patched_images/18897/1
./SD/patched_images/18897/1/img.png
./SD/patched_images/34261/0
./SD/patched_images/34261/0/img.png
./SD/patched_images/953/1
./SD/patched_images/953/1/img.png
./SD/patched_images/47793/0
./SD/patched_images/47793/0/img.png
./SD/patched_images/2828/1
./SD/patched_images/2828/1/img.png
./SD/patched_images/22304/0
./SD/patched_images/22304/0/img.png
./SD/patched_images/16131/1
./SD/patched_images/16131/1/img.png
./SD/patched_images/46641/1
./SD/patched_images/

...

./SD/patched_images/28484/1
./SD/patched_images/28484/1/img.png
./SD/patched_images/47529/0
./SD/patched_images/47529/0/img.png
./SD/patched_images/35935/0
./SD/patched_images/35935/0/img.png
./SD/patched_images/22982/0
./SD/patched_images/22982/0/img.png
./SD/patched_images/8794/0
./SD/patched_images/8794/0/img.png
./SD/patched_images/9646/0
./SD/patched_images/9646/0/img.png
./SD/patched_images/48561/0
./SD/patched_images/48561/0/img.png
./SD/patched_images/43189/1
./SD/patched_images/43189/1/img.png
./SD/patched_images/23850/1
./SD/patched_images/23850/1/img.png
./SD/patched_images/18211/0
./SD/patched_images/18211/0/img.png
./SD/patched_images/29764/1
./SD/patched_images/29764/1/img.png
./SD/patched_images/3972/1
./SD/patched_images/3972/1/img.png
./SD/patched_images/49681/1
./SD/patched_images/49681/1/img.png
./SD/patched_images/42269/0
./SD/patched_images/42269/0/img.png
./SD/patched_images/12519/1
./SD/patched_images/12519/1/img.png
./SD/patched_images/18023/0
./SD/patched_image

./SD/patched_images/10679/0
./SD/patched_images/10679/0/img.png
./SD/patched_images/37867/1
./SD/patched_images/37867/1/img.png
./SD/patched_images/6837/0
./SD/patched_images/6837/0/img.png
./SD/patched_images/18414/0
./SD/patched_images/18414/0/img.png
./SD/patched_images/48364/0
./SD/patched_images/48364/0/img.png
./SD/patched_images/9043/1
./SD/patched_images/9043/1/img.png
./SD/patched_images/3579/0
./SD/patched_images/3579/0/img.png
./SD/patched_images/8191/0
./SD/patched_images/8191/0/img.png
./SD/patched_images/28281/1
./SD/patched_images/28281/1/img.png
./SD/patched_images/23669/1
./SD/patched_images/23669/1/img.png
./SD/patched_images/29353/0
./SD/patched_images/29353/0/img.png
./SD/patched_images/12912/1
./SD/patched_images/12912/1/img.png
./SD/patched_images/48156/1
./SD/patched_images/48156/1/img.png
./SD/patched_images/2699/0
./SD/patched_images/2699/0/img.png
./SD/patched_images/9271/0
./SD/patched_images/9271/0/img.png
./SD/patched_images/47922/1
./SD/patched_images/4792

./SD/patched_images/46832/0
./SD/patched_images/46832/0/img.png
./SD/patched_images/8361/0
./SD/patched_images/8361/0/img.png
./SD/patched_images/3789/0
./SD/patched_images/3789/0/img.png
./SD/patched_images/49046/0
./SD/patched_images/49046/0/img.png
./SD/patched_images/48194/0
./SD/patched_images/48194/0/img.png
./SD/patched_images/27039/0
./SD/patched_images/27039/0/img.png
./SD/patched_images/720/0
./SD/patched_images/720/0/img.png
./SD/patched_images/7329/1
./SD/patched_images/7329/1/img.png
./SD/patched_images/31960/1
./SD/patched_images/31960/1/img.png
./SD/patched_images/23499/1
./SD/patched_images/23499/1/img.png
./SD/patched_images/28071/1
./SD/patched_images/28071/1/img.png
./SD/patched_images/27805/0
./SD/patched_images/27805/0/img.png
./SD/patched_images/4331/0
./SD/patched_images/4331/0/img.png
./SD/patched_images/45016/0
./SD/patched_images/45016/0/img.png
./SD/patched_images/32978/0
./SD/patched_images/32978/0/img.png
./SD/patched_images/21553/0
./SD/patched_images/2155

./SD/patched_images/30284/0
./SD/patched_images/30284/0/img.png
./SD/patched_images/27233/0
./SD/patched_images/27233/0/img.png
./SD/patched_images/13006/1
./SD/patched_images/13006/1/img.png
./SD/patched_images/7123/0
./SD/patched_images/7123/0/img.png
./SD/patched_images/46204/0
./SD/patched_images/46204/0/img.png
./SD/patched_images/8957/1
./SD/patched_images/8957/1/img.png
./SD/patched_images/16574/0
./SD/patched_images/16574/0/img.png
./SD/patched_images/22741/1
./SD/patched_images/22741/1/img.png
./SD/patched_images/23693/1
./SD/patched_images/23693/1/img.png
./SD/patched_images/9885/1
./SD/patched_images/9885/1/img.png
./SD/patched_images/34624/1
./SD/patched_images/34624/1/img.png
./SD/patched_images/8359/1
./SD/patched_images/8359/1/img.png
./SD/patched_images/31164/0
./SD/patched_images/31164/0/img.png
./SD/patched_images/42496/0
./SD/patched_images/42496/0/img.png
./SD/patched_images/27001/0
./SD/patched_images/27001/0/img.png
./SD/patched_images/718/1
./SD/patched_images/71

AttributeError: 'tuple' object has no attribute 'split'

In [13]:
os.getcwd()

'/Users/as186233/Documents/AhsansPersonal/psvrt/base_line_exp/notebook'

In [41]:
mv_dir = "./SD/patched_images/39386/1/img.png".split("SD/patched_images/")[1].split("/")[0]
mv_dir = "../../original_images/SD/" + mv_dir

In [42]:
mv_dir

'../../original_images/SD/39386'

In [46]:
copytree(mv_dir,"./SD/original_images/39386")

'./SD/original_images/39386'